In [5]:
import json
from bs4 import BeautifulSoup
from collections import OrderedDict
import re

# set up the corpus object
# and wtf does it being a translation suggest we do :O
# now the work
corpus = OrderedDict()
corpus["author"] = [{"name": "A. S. Kline"}, {"slug": "tony-kline"}, {"full name": "Tony Kline"}, {"abbreviation": "A. Kl."}]
works_list = []


# includes Amores, Ars Amatoria, and Remedia
html_file = "Kline_Love_Poems.html"
# just Heroides
heroides_file = "Heroides.htm"

html_doc = open(html_file).read()
soup = BeautifulSoup(html_doc, 'html.parser')

def get_amores(works_list):
    # article tags surround works, all other tags are unnested, boo
    for index, work in enumerate(soup.findAll('article')):
        # ignore the preface material
        if index==1:
            # the h1 is the title
            work_dict = OrderedDict() # otherwise the title is last which is not what we want in the JSON
            work_dict["title"] = "Heroides"
#             work_dict["abbreviation"] = work.attrib["n"]
            work_dict["slug"] = "amores"
            
            
            books_list = []
            book_looping = True
            # only h2s with this class indicate Book titles
            for index, book in enumerate(work.findAll('h2', class_='text-align-center'), start=1):
                book_dict = OrderedDict()
                book_dict["book_index"] = index
                book_dict["book_title"] = book.text
                
                poems_list = []
                poem_looping = True
                
                # hack to let first book's epigram have a zero index
                if index == 1:
                    start_num = 0
                else:
                    start_num = 1
                # begin poem loop
                for index, poem in enumerate(book.find_next_siblings('h3'), start=start_num):
                    lines_list = []
                    poem_dict = OrderedDict()
                    poem_dict["poem_index"] = index
                    poem_dict["poem_title"] = poem.text
                    line_looping = True
                    # begin line loop
                    for index, line in enumerate(poem.find_next_siblings(), start=1):
                        line_dict = {}
                        line_dict["line_index"] = index
                        line_dict["meter"] = "none"
                        try:
                            tag_name = line.name
                        except AttributeError:
                            tag_name = ""
                        if tag_name == "p":
                            text = line.text
                            line_dict["text"] = text
                            lines_list.append(line_dict)
                        elif tag_name == "hr":
                            line_looping = False
                            poem_looping = False
                        else:
                            line_looping = False
                            # this break just puts us back into the h3 loop
                            break
                    poems_list.append(poem_dict)
                    if not poem_looping:
                        break
                book_dict["poems"]= poems_list
                books_list.append(book_dict)
            work_dict["books"] = books_list
            works_list.append(work_dict)

def get_ars(works_list):
    # article tags surround works, all other tags are unnested, boo
    for index, work in enumerate(soup.findAll('article')):
        # get the Ars
        if index==2:
            # the h1 is the title
            work_dict = OrderedDict() # otherwise the title is last which is not what we want in the JSON
            work_dict["title"] = work.find('h1').text
#             work_dict["abbreviation"] = work.attrib["n"]
            work_dict["slug"] = "ars"
            
            books_list = []
            book_looping = True
            # only h2s with this class indicate Book titles
            for index, book in enumerate(work.findAll('h2', class_='text-align-center'), start=1):
                book_dict = OrderedDict()
                book_dict["book_index"] = index
                book_dict["book_title"] = book.text
               
                poem_dict = OrderedDict()
                poem_dict["poem_index"] = 1
                poem_dict["poem_title"] = "Poem 1"
                
                poems_list = []
                lines_list = []
                line_looping = True
                anchor = book.find_next_sibling('h3')
                for index, line in enumerate(anchor.find_next_siblings('p'), start=1):
                    line_dict = {}
                    line_dict["line_index"] = index
                    line_dict["meter"] = "none"
                    try:
                        tag_name = line.name
                    except AttributeError:
                        tag_name = ""
                    if tag_name == "p":
                        text = line.text
#                         print text
                        line_dict["text"] = text
                        lines_list.append(line_dict)
                    elif tag_name == "hr":
                        line_looping = False
                        book_looping = False
                poem_dict['lines'] = lines_list
                poems_list.append(poem_dict)
                if not book_looping:
                    break
            book_dict["poems"]= poems_list
            books_list.append(book_dict)
            work_dict["books"] = books_list
            works_list.append(work_dict)

# wherein we confront the bugbear of MS-Word-generated html :(            
def get_heroides(works_list):
    bad_doc = open(heroides_file).read()
    soup = BeautifulSoup(bad_doc, 'html.parser')
    
    work_dict = OrderedDict() # otherwise the title is last which is not what we want in the JSON
    work_dict["title"] = "Heroides"
#   work_dict["abbreviation"] = work.attrib["n"]
    work_dict["slug"] = "heroides"
    
    book_dict = OrderedDict()
    book_dict["book_index"] = 1
    book_dict["book_title"] = "Book 1"
    
    books_list = []
    
    for index, poem in enumerate(soup.findAll('h1'), start=1):
        print "poem number " + str(index)
        title = poem.get_text()
        title = title.split(':')[1]
        title = ' '.join(title.split())
        
        poem_dict = OrderedDict()
        poem_dict["poem_index"] = index
        poem_dict["poem_title"] = title
        
        poems_list = []
        lines_list = []
        
        is_looping = True
        for index, line in enumerate (poem.find_next_siblings('p'), start =1):
            line_dict = {}
            line_dict["line_index"] = index
            line_dict["meter"] = "none"
    
            line = line.find_next_sibling()
            try:
                tag_name = line.name
            except AttributeError:
                tag_name = ""
            if tag_name == "p":
                # take care of weird new lines etc. in the html
                text = ' '.join(line.text.split())
                line_dict["text"] = text
                lines_list.append(line_dict)
                print text
            else:
                is_looping = False
                break
            if not is_looping:
                break
            poem_dict['lines'] = lines_list
            poems_list.append(poem_dict)
    book_dict["poems"]= poems_list
    books_list.append(book_dict)
    work_dict["books"] = books_list
    works_list.append(work_dict) 
    
get_heroides(works_list)
corpus["works"]=works_list

json_corpus = json.dumps(corpus)
print json_corpus

# structure notes
#poems have individual anchor links , so for Amores, start anchor_Toc520535255 end anchor_Toc520536672
# basic html structure -- not much nesting :/
# <article> #indicates work
# <h1 id="Amoreshome">The Amores</h1> #indicates title of work
# <h2 class="text-align-center" id="Amoresbk1">Book I</h2> #indicates book num, has class, has hr beforehand
# <h2>Contents</h2> #hanging out, does not have class
# <h3><a id="anchor_Toc520535255">His Epigram</a></h3> #actual poems have h3 at head, no surrounding tags
# <h2 class="text-align-center" id="Amoresbk2">Book II</h2>
# <h2>Contents</h2>
# <h3><a id="anchor_Toc520535255">His Epigram</a></h3>
# <h2 class="text-align-center" id="Amoresbk3">Book III</h2>
# <h2>Contents</h2>
# </article> #ends just after p of last poem
# h2 Amatoriabk1
# end of book:
# <hr />
# <h2 class="text-align-center" id="Amoresbk2">Book II</h2>


# other notes
# https://stackoverflow.com/questions/11647348/find-next-siblings-until-a-certain-one-using-beautifulsoup
# https://stackoverflow.com/questions/2077897/substitute-multiple-whitespace-with-single-whitespace-in-python
# https://stackoverflow.com/questions/24878437/cant-remove-line-breaks-from-beautifulsoup-text-output-python-2-7-5

poem number 1
Your Penelope sends you this, Ulysses, the so-long-delayed.
Don’t reply to me however: come yourself.
Troy lies in ruins, an enemy, indeed, to the girls of Greece -
Priam, and all of Troy, were scarcely worth this!
O I wish, at that time when he sought Sparta with his fleet,
Paris, the adulterer, had been whelmed beneath angry seas!
I would not have lain here, cold in an empty bed,
nor be left behind, to complain, at suffering long days,
nor my hand, bereft, exhaust me, working all night long
to cause deception, with my doubtful web.
When have I not feared dangers worse than all realities?
Love is a thing full of anxious fears.
I imagined the Trojans’ violent attacks on you:
often I grew pale at Hector’s name:
if someone told of Antilochus defeated by Hector,
Antilochus was the reason for my fears,
if of Patroclus, dying in Achilles’s armour,
I wept that tricks might fail of success.
Tlepolemus warmed the spear of Sarpedon with blood,
Tlepolemus’s death is then a new caus